In [1]:
import os
os.listdir('../../scripts')
import sys
sys.path.append('../../Scripts')

In [2]:
from generate_signals import SignalGenerator
from preprocess_daily import DailyPreprocessor

In [3]:
inter_no = 175
Node_id = 'i0'

In [4]:
# desired result
self = SignalGenerator()
self.prepare_data()
self.process_history()
self.process_movement()
self.make_histids()
self.set_timepoints()
self.assign_red_yellow()
self.SIGTABLE

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.


inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704418730       1       1       8       4        33   
1         178     c30  1704418730       1       1       8       4         4   
2         178     c30  1704418730       2       2       7       3         1   
0         178     c30  1704418730       2       2       7       3        34   
1         178     c30  1704418730       2       2       7       3         4   
..        ...     ...         ...     ...     ...     ...     ...       ...   
2         210     u60  1704419299       3       3       7       4         1   
0         210     u60  1704419299       3       3       7       4        65   
1         210     u60  1704419299       3       3       7       4         4   
2         210     u60  1704419299       4       4       8       3         1   
237       210     u60  1704419299       4       4       8       3        19   

         state phase_sumo  
0       gggggg        0_g  
1       gggggg        0_y  
2       gggggg       1__r  
0       GGGGGG        1_g  
1       GGGGGG        1_y  
..         ...        ...  
2    ggggggggr       3__r  
0    ggggggggr        3_g  
1    ggggggggr        3_y  
2    ggggggggr       4__r  
237  ggggggggr        4_g  

[684 rows x 10 columns]

In [5]:
self = SignalGenerator()
self.prepare_data()
self.process_history()
self.process_movement()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.


In [6]:
self.merge_dfs()

In [7]:
# 4-2. histid
self.histid = self.movedur.copy()
self.histid['node_id'] = self.histid['inter_no'].map(self.inter2node)
histid_start = self.present_time - 600
self.histid = self.histid[self.histid.start_unix > histid_start]

mapping_dict = self.matching.set_index(['node_id', 'move_no'])['state'].to_dict()

for i, row in self.histid.iterrows():
    node_id = row.node_id
    move_A = row.move_A
    move_B = row.move_B
    
    # A링의 state 지정
    if (node_id, move_A) in mapping_dict:
        state_A = mapping_dict[(node_id, move_A)]
    else:
        state_A = ''.join(self.node2init[node_id])
    self.histid.at[i, 'state_A'] = state_A

    # B링의 state 지정
    if (node_id, move_B) in mapping_dict:
        state_B = mapping_dict[(node_id, move_B)]
    else:
        state_B = ''.join(self.node2init[node_id])
    self.histid.at[i, 'state_B'] = state_B    

In [8]:
# 4-3. histids
new_histids = []
for parent_id in self.parent_ids:
    for child_id in self.pa2ch[parent_id]:
        new_histid = self.histid.copy()[self.histid.node_id==parent_id].drop(columns=['state_A', 'state_B'])
        # new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
        for i, row in new_histid.iterrows():
            phas_A = row.phas_A
            phas_B = row.phas_B
            new_match = self.match6[self.match6.node_id==child_id]
            Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]

            # A링의 state 지정
            state_A = Arow.iloc[0].state
            new_histid.at[i, 'state_A'] = state_A

            # B링의 state 지정
            Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
            state_B = Brow.iloc[0].state
            new_histid.at[i, 'state_B'] = state_B

            new_histid.at[i, 'node_id'] = child_id
        new_histids.append(new_histid)
import pandas as pd
new_histids = pd.concat(new_histids)
self.histids = pd.concat([self.histid.copy(), new_histids])
self.histids = self.histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
self.histids = self.histids[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration', 'state_A', 'state_B']]
self.histids.query('node_id==@Node_id')

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         175      i0  1704418520       1       1       8       4        43   
1         175      i0  1704418520       2       2       7       3        45   
2         175      i0  1704418520       3       3       6       1        33   
3         175      i0  1704418520       3       4       6       2        22   
4         175      i0  1704418520       4       4       5       2        37   
62        175      i0  1704418699       1       1       8       4        43   
63        175      i0  1704418699       2       2       7       3        45   
64        175      i0  1704418699       3       3       6       1        33   
65        175      i0  1704418699       3       4       6       2        22   
66        175      i0  1704418699       4       4       5       2        37   
131       175      i0  1704418880       1       1       8       4        43   
132       175      i0  1704418880       2       2       7       3        45   
133       175      i0  1704418880       3       3       6       1        33   
134       175      i0  1704418880       3       4       6       2        22   
135       175      i0  1704418880       4       4       5       2        37   
193       175      i0  1704419060       1       1       8       4        43   
194       175      i0  1704419060       2       2       7       3        45   
195       175      i0  1704419060       3       3       6       1        33   
196       175      i0  1704419060       3       4       6       2        22   
197       175      i0  1704419060       4       4       5       2        37   
259       175      i0  1704419240       1       1       8       4        43   
260       175      i0  1704419240       2       2       7       3        45   
261       175      i0  1704419240       3       3       6       1        33   
262       175      i0  1704419240       3       4       6       2        22   
263       175      i0  1704419240       4       4       5       2        37   
337       175      i0  1704419420       1       1       8       4        43   
338       175      i0  1704419420       2       2       7       3        45   
339       175      i0  1704419420       3       3       6       1        33   
340       175      i0  1704419420       3       4       6       2        22   
341       175      i0  1704419420       4       4       5       2        37   
380       175      i0  1704419520       1       1       8       4        24   
381       175      i0  1704419520       2       2       7       3        25   
382       175      i0  1704419520       3       3       6       1        18   
383       175      i0  1704419520       3       4       6       2        13   
384       175      i0  1704419520       4       4       5       2        20   

               state_A            state_B  
0    grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
1    grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
2    grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
3    grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
4    grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
62   grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
63   grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
64   grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
65   grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
66   grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
131  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
132  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
133  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
134  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
135  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
193  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
194  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
195  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
196  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
197  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
259  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
260  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
261  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
262  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
263  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
337  grrrgrrrgGG

In [9]:
self.set_timepoints()

In [12]:
self.sigtable

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704418730       1       1       8       4        38   
1         178     c30  1704418730       2       2       7       3        39   
2         178     c30  1704418730       3       3       5       2        43   
3         178     c30  1704418730       4       4       6       1        22   
4         178     c30  1704418900       1       1       8       4        38   
..        ...     ...         ...     ...     ...     ...     ...       ...   
233       210     u60  1704419299       1       1       6      18        28   
234       210     u60  1704419299       1       2       6       2        15   
235       210     u60  1704419299       2       2       5       2        43   
236       210     u60  1704419299       3       3       7       4        70   
237       210     u60  1704419299       4       4       8       3        24   

       state_A    state_B  phase_sumo  
0       gggggg     gggggg           0  
1       GGGggg     gggGGG           1  
2       GGGggg     gggGGG           2  
3       GGGggg     gggGGG           3  
4       gggggg     gggggg           0  
..         ...        ...         ...  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4  

[238 rows x 11 columns]

In [73]:
def get_red(pre_state:str, cur_state:str):
    assert len(pre_state) == len(cur_state), "cur_state, nex_state의 길이가 서로 다릅니다."
    state_r = ''
    for c, n in zip(pre_state, cur_state):
        if c == n:
            state_r += c
        elif (c == 'r') and (n == 'G'):
            state_r += 'r'
        elif (c == 'G') and (n == 'r'):
            state_r += 'r'
        else:
            raise ValueError(f"예상치 못한 신호조합: current={c}, next={n}")
    return state_r

def get_yellow(cur_state:str, nex_state:str):
    assert len(cur_state) == len(nex_state), "cur_state, nex_state의 길이가 서로 다릅니다."
    state_y = ''
    for c, n in zip(cur_state, nex_state):
        if c == n:
            state_y += c
        elif (c == 'r') and (n == 'G'):
            state_y += 'r'
        elif (c == 'G') and (n == 'r'):
            state_y += 'y'
        else:
            raise ValueError(f"예상치 못한 신호조합: current={c}, next={n}")
    return state_y

def cumulate(sig, alph):
    csig = [] # cumulated sig
    pre = pd.Series({f'phas_{alph}':None})

    start_time = 0
    elapsed = 0
    for i, cur in sig.iterrows():
        start_unix = cur.start_unix
        
        # pre, nex
        if i != 0:
            pre = sig.iloc[i-1]
        
        if i != len(sig) - 1:
            nex = sig.iloc[i+1]
        
        # duration
        if cur[f'phas_{alph}'] == nex[f'phas_{alph}']:
            continue
        if cur[f'phas_{alph}'] == pre[f'phas_{alph}']:
            duration = cur.duration + pre.duration
        else:
            duration = cur.duration
        start_times = []
        states = []
        phases = []

        # red
        if i != 0:
            start_time += elapsed
            start_times.append(start_time)
            states.append(get_red(pre[f'state_{alph}'], cur[f'state_{alph}']))
            phases.append(f'{cur[f"phas_{alph}"]}r')

            elapsed = cur[f'red_{alph}']

        # green
        if i == 0:
            start_time = 0
        else:
            start_time += elapsed
        start_times.append(start_time)
        states.append(cur[f'state_{alph}'])
        phases.append(f'{cur[f"phas_{alph}"]}g')
        if i == 0:
            elapsed = duration - cur[f'yellow_{alph}']
        else:
            elapsed = duration - cur[f'yellow_{alph}'] - cur[f'red_{alph}']

        # yellow
        if i != len(sig) - 1:
            start_time += elapsed
            start_times.append(start_time)
            states.append(get_yellow(cur[f'state_{alph}'], nex[f'state_{alph}']))
            phases.append(f'{cur[f"phas_{alph}"]}y')
            elapsed = cur[f'yellow_{alph}']
        sig_ = pd.DataFrame({'start_time':start_times, f'phas_{alph}':phases, f'state_{alph}':states})
        sig_['start_unix'] = start_unix
        csig.append(sig_)
    csig = pd.concat(csig).reset_index(drop=True)
    return csig

In [80]:
import time
now = time.time()
self.SIGTABLE = []
for node_id in self.sigtable.node_id.unique():
    sig = self.sigtable.query('node_id==@Node_id')
    for i, row in sig.iterrows():
        inter_no = row.inter_no
        phas_A = row.phas_A
        phas_B = row.phas_B
        start_unix = row.start_unix
        prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
        red_A    = prow[f'red_A{phas_A}']
        yellow_A = prow[f'yellow_A{phas_A}']
        red_B    = prow[f'red_B{phas_B}']
        yellow_B = prow[f'yellow_B{phas_B}']
        sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B
    sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                    'phas_A':str, 'phas_B':str})
    sig = sig.drop(['move_A','move_B'], axis=1)

    sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
    sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)

    csig_A = cumulate(sig_A, 'A')
    csig_B = cumulate(sig_B, 'B')

    SIG = pd.merge(csig_A, csig_B, on=['start_time', 'start_unix'], how='outer')
    SIG = SIG.sort_values(by='start_time').reset_index(drop=True)
    SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
    SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
    SIG['phase'] = SIG['phas_A'] + "_" + SIG['phas_B']
    SIG['node_id'] = node_id
    SIG = SIG[['node_id', 'start_unix', 'start_time', 'phase', 'state_A', 'state_B']]
    SIG['duration'] = SIG['start_time'].shift(-1) - SIG['start_time']
    SIG = SIG[:-1]
    SIG['duration'] = SIG['duration'].astype(int)
    for row in SIG.itertuples():
        state = ''
        for a, b, in zip(row.state_A, row.state_B):
            if a == 'r':
                state += b
            elif b == 'r':
                state += a
            elif a == b:
                state += a
            else:
                raise ValueError(f"예상되지 않은 조합 발생: a={a}, b={b}")
        SIG.at[row.Index, 'state'] = state
    SIG = SIG.drop(columns=['start_time', 'state_A', 'state_B'])
    self.SIGTABLE.append(SIG)
self.SIGTABLE = pd.concat(self.SIGTABLE)
self.SIGTABLE
print(time.time() - now)

0.6265964508056641
